In [0]:
project_name = 'test_project_1'
#permissions='default'
permissions='fulldata'

In [0]:
pip install pycountry

Python interpreter will be restarted.
  Installing build dependencies: started
  Installing build dependencies: finished with status 'done'
  Getting requirements to build wheel: started
  Getting requirements to build wheel: finished with status 'done'
    Preparing wheel metadata: started
    Preparing wheel metadata: finished with status 'done'
  Created wheel for pycountry: filename=pycountry-22.3.5-py2.py3-none-any.whl size=10681845 sha256=fae2f0ef4b4fa492eec856bbee664b90be1a88a9363c5268d0457fe8ac8f6c32
  Stored in directory: /root/.cache/pip/wheels/47/15/92/e6dc85fcb0686c82e1edbcfdf80cfe4808c058813fed0baa8f
Successfully built pycountry
Python interpreter will be restarted.


In [0]:
%run /Snippets/header_008

PROJECT DETAILS:
Project identifier: test_project_1
Cluster data access level: fulldata


EXECUTION DETAILS:
Spark version: 11.3.x-scala2.12, 
Cluster Node Type: i3.xlarge, 
Driver Node Type: c4.2xlarge, 
Worker Node Type: i3.xlarge


DATA SNAPSHOT DETAILS:
This notebook uses the latest snapshot date for this version: "v008.20231003094404/", (03 October 2023)

 The following are the Scopus snapshot dates available for datasets at v008:
['v008.20220314092239/', 'v008.20220906063204/', 'v008.20221021151538/', 'v008.20230509104116/', 'v008.20230821105000/', 'v008.20231003094404/']
(If you want to use a different snapshot, in the first cell of your notebook, set the variable `custom_snapshot_date` to one of the options listed above (string data type))



DATA SAMPLE DETAILS:
Setting paths to run on full datasets (100% Scopus publication volume)


In [0]:
import pandas as pd
import pyspark.sql.functions as F
def first(lst):
  return lst[0]
def extract_publication_info(newdf):
  #newdf = df_ani.limit(50)
  newdf = newdf.select('doi','Eid','year','Au','Au_Af','Au_cors','publication_type','openaccess','issn','source','news_cnt','correspondence','Af')


  newdf = newdf.withColumn('Au1', first(newdf['Au']))



  newdf = newdf.withColumn('Au2', F.element_at(newdf['Au'], -1))

  newdf = newdf.withColumn('num_au', F.size(newdf['Au']))

  newdf = newdf.withColumn('Au1_id', F.col('Au1').getItem('auid'))

  newdf = newdf.withColumn('Au2_id', F.col('Au2').getItem('auid'))

  newdf = newdf.withColumn('Au_cor_id', F.col('Au_cors').getItem('auid'))
  #newdf = newdf.withColumn('Au_cor_name', F.col('Au_cors').getItem('given_name'))
  #newdf = newdf.withColumn('cor1_given_name', first(newdf['Au_cor_name']))

  newdf = newdf.withColumn('cor_seq', F.col('Au_cors').getItem('Authorseq'))
  newdf = newdf.withColumn('cor_seq_first', first(newdf['cor_seq']))

  newdf = newdf.withColumn('auth_seq', F.col('Au_Af').getItem('Authorseq'))
  newdf = newdf.withColumn('aff_seq', F.col('Au_Af').getItem('affiliation_seq'))
  newdf = newdf.withColumn("auth_pos", F.expr("array_position(auth_seq, cor_seq_first)"))

  newdf = newdf.withColumn("auth_pos", newdf["auth_pos"].cast(IntegerType()))  
  #newdf = newdf.filter(F.col('aff_seq').isNotNull())
  newdf = newdf.filter(F.col('auth_pos') != 0)
  newdf = newdf.withColumn("aff", F.element_at(newdf['aff_seq'], newdf['auth_pos']))
  newdf = newdf.withColumn("aff_val", F.element_at(newdf['Af'], newdf['aff']))
  newdf = newdf.withColumn("cor_afid", F.col('aff_val').getItem('afid'))

  newdf = newdf.withColumn('given_seq', F.col('Au').getItem('given_name'))
  newdf = newdf.withColumn("cor1_given_name", F.element_at(newdf['given_seq'], newdf['cor_seq_first']))
  display(newdf.limit(10))

  return newdf
def get_smc_classification(newdf):
  df_smc_ani = spark.read.format("parquet").load(basePath+tablename_smc_complete)
  newdf2 = newdf.join(df_smc_ani,'Eid', 'inner')
  return newdf2

def get_gender(newdf):
  df_gender = spark.read.format("parquet").load(basePath+tablename_gender_inference)
  #non_null_count = newdf.where(F.col('Au1_id').isNotNull()).count()
  mergedf = df_gender.join(newdf, newdf.Au1_id == df_gender.auid, 'inner').select(
      df_gender.Inferred_Probable_Gender,newdf.doi,newdf.news_cnt,newdf.Au,newdf.Eid, newdf.year, newdf.publication_type,newdf.openaccess, newdf.issn, 
      newdf.num_au, newdf.Au1_id,newdf.Au2_id,newdf.Au_cor_id, newdf.srcid, newdf.subfield_article, newdf.subfield_journal, newdf.subfield_hybrid,newdf.correspondence,
      newdf.cor1_given_name, newdf.cor_afid)
  mergedf = mergedf.withColumnRenamed('Inferred_Probable_Gender', 'Au1_gender')

  mergedf2 = df_gender.join(mergedf, mergedf.Au2_id == df_gender.auid, 'inner').select(
      df_gender.Inferred_Probable_Gender, mergedf.doi,mergedf.news_cnt,mergedf.Au,mergedf.Eid, mergedf.year, mergedf.publication_type,mergedf.openaccess, mergedf.issn, 
      mergedf.num_au, mergedf.Au1_id,mergedf.Au2_id,mergedf.Au_cor_id, mergedf.srcid, mergedf.subfield_article, mergedf.subfield_journal, mergedf.subfield_hybrid, mergedf.Au1_gender,mergedf.correspondence,mergedf.cor1_given_name,mergedf.cor_afid)
  mergedf2 = mergedf2.withColumnRenamed('Inferred_Probable_Gender', 'Au2_gender')

  #mergedf2 = mergedf2.withColumn('no_cor', F.size(mergedf2['Au_cor_id']))
  #display("len os final4 ", mergedf2.count(),"\n")

  mergedf2 = mergedf2.withColumn('cor_au1', first(mergedf2['Au_cor_id']))

  xxx = mergedf2.select('Au_cor_id') ######################
  xxx = xxx.withColumn('num', F.size(xxx['Au_cor_id']))
  display("len of xxx ",xxx.count(),"\n")
  xx = xxx.filter(func.col('num') > 1)
  display("len of xxx ",xx.count(),"\n") ############
  #display(xx.limit(10))

  ########### checknumber here

  #display(final_data4.limit(20))

  mergedf3 = mergedf2.filter(F.col('cor_au1').isNotNull())
  display("no of not null cor au",mergedf3.count(),"\n")

  mergedf4 = df_gender.join(mergedf3, mergedf3.cor_au1 == df_gender.auid, 'inner').select(
      df_gender.Inferred_Probable_Gender, mergedf3.doi,mergedf3.news_cnt,mergedf3.Au,mergedf3.Eid, mergedf3.year, mergedf3.publication_type,mergedf3.openaccess, mergedf3.issn, 
      mergedf3.num_au, mergedf3.Au1_id,mergedf3.Au2_id,mergedf3.Au_cor_id, mergedf3.srcid, mergedf3.subfield_article, mergedf3.subfield_journal, mergedf3.subfield_hybrid, mergedf3.Au1_gender,mergedf3.Au2_gender,mergedf3.cor_au1,mergedf3.correspondence,mergedf3.cor1_given_name, mergedf3.cor_afid)
  mergedf4 = mergedf4.withColumnRenamed('Inferred_Probable_Gender', 'cor_gender')

  return mergedf4

def merge_news_cnt(scop):
  scop = scop.filter(func.col('year') >= 2018)
  scop = scop.filter(func.col('year') <= 2022)
  df1 = spark.read.format("csv").option("header", "true").load("dbfs:/FileStore/shared_uploads/arabi2@wisc.edu/doi_news_final.csv")
  display("# doi data from crossref and altmetric ",df1.count(),"\n")
  df = scop.join(df1, 'doi','inner')
  df = df.withColumn("news_cnt", df["news_cnt"].cast(IntegerType()))
  return df

from pyspark.sql.functions import lower

df_ani = spark.read.format("parquet").load(basePath+tablename_ani)

display("len of df_ani ",df_ani.count(),"\n")
dd = df_ani.withColumn('language', first(df_ani['meta_language']))
d1 = dd.withColumn('language_s', lower(dd['language']))

d2 = d1.filter(func.col('language_s') == 'english')
display("len of df_ani in english ",d2.count(),"\n")

with_news = merge_news_cnt(d2)
display("merged data len between crossref and scopus ",with_news.count(),"\n")

newdf = extract_publication_info(with_news)

df_class = get_smc_classification(newdf)
final_data = get_gender(df_class)
display(final_data.count(),"\n")
final_data2 = final_data.dropna(subset=["doi"])
display(final_data2.count(),"\n")

##extracting sci_val topic for each publication
df_top_eids = spark.read.format("parquet").load(basePath+tablename_top_topic_eid)

final_data3 = final_data2.join(df_top_eids,'Eid','inner')
#display(final_data3.count())
display(final_data3.limit(10))


import pyspark.sql.functions as F
import pyspark.sql.column as C

def find_sjr(met,yy,yr):

  ylst = F.tolist(yy)

  #index = ylst.index(yr)
  #sjr = m[index]
  return m


df_sources = spark.read.format("parquet").load(basePath+tablename_sources)

data = final_data3.join(df_sources,'srcid','inner').select(df_sources.metrics_calculations,df_sources.sourcetitle,df_sources.openaccess_status,final_data3.srcid,final_data3.doi,final_data3.news_cnt,final_data3.year,
final_data3.publication_type, final_data3.issn, final_data3.num_au,final_data3.Au1_id, final_data3.subfield_article,final_data3.subfield_journal, final_data3.Au1_gender,final_data3.TopicId, 
final_data3.cor_gender,final_data3.cor_au1,final_data3.correspondence, final_data3.cor1_given_name, final_data3.cor_afid)

display("len of merged data between src ", data.count(),"\n")

data = data.withColumn('SJR_lst', F.col('metrics_calculations').getItem('SJR'))
data = data.withColumn('year_SJR', F.col('metrics_calculations').getItem('year'))

#data = data.withColumn('SJR', find_sjr(data['SJR_lst'],data['year_SJR'], data['year']))
data = data.withColumn("pos", F.expr("array_position(year_SJR, year)"))


data = data.withColumn("pos", data["pos"].cast(IntegerType()))  
data = data.withColumn("SJR", F.element_at(data['SJR_lst'], data['pos']))

data = data.withColumn('cor_af', first(data['correspondence']))
data = data.withColumn('cor_coun', F.col('cor_af').getItem('country'))



import pycountry
import pyspark.sql.functions as F

def convert_country_short_name(country_short_name):
  #country = pycountry.countries.get(alpha_2=country_short_name)
  if len(country_short_name) == 3:
    country = pycountry.countries.get(alpha_3=country_short_name)
  else:
    country = pycountry.countries.get(alpha_2=country_short_name)

  return country.name if country else None

@F.udf(returnType=F.StringType())
def my_udf(country_short_name):
  return convert_country_short_name(country_short_name)

data = data.filter(F.col('cor_coun').isNotNull())
data = data.withColumn("country_name", my_udf(data["cor_coun"]))
#un_full_coun = un_name.withColumn("country_name", my_udf(un_name["cor_coun"]))

df_ipr = spark.read.format("parquet").load(basePath+tablename_ipr)
data = data.join(df_ipr,[data.cor_afid == df_ipr.afid],'inner')
display(data.limit(10))

val_data = data.filter(func.col('cor_gender') != 'unknown')

#val_un = data.filter(func.col('cor_gender') == 'unknown')



display("len of data whose cor_gender is not unknown ",val_data.count(),"\n")

display(val_data.limit(5),"\n")


#val_un = data.filter(func.col('cor_gender') == 'unknown')
df_apr = spark.read.format("parquet").load(basePath+tablename_apr)
#un_full_coun = val_un.join(df_apr,val_un.cor_au1 == df_apr.auid,'inner')
un_full_coun = data.filter(func.col('cor_gender') == 'unknown')

display("len of unknown name ", un_full_coun.count(),"\n")
un_full_coun = un_full_coun.filter(F.col('cor1_given_name').isNotNull())
un_full_coun = un_full_coun.filter(F.col('country_name').isNotNull())
display("len of unknown name after dropping null country and given name ", un_full_coun.count(),"\n")
df_wos = spark.read.format("csv").option("header", "true").load("dbfs:/FileStore/shared_uploads/arabi2@wisc.edu/wos_gender_firstname.csv")
#df_wos.printSchema()
#df_wos = df_wos.filter(func.col('country') == 'China')
newfile = un_full_coun.join(df_wos,[un_full_coun.cor1_given_name == df_wos.givenname,un_full_coun.country_name == df_wos.country],'inner')
display("len or merged gender with wos ", newfile.count(),"\n")

'len of df_ani '95242081'\n''len of df_ani in english '83156711'\n''# doi data from crossref and altmetric '9061001'\n''merged data len between crossref and scopus '6609667'\n'

doi Eid year Au Au_Af Au_cors publication_type openaccess issn source news_cnt correspondence Af Au1 Au2 num_au Au1_id Au2_id Au_cor_id cor_seq cor_seq_first auth_seq aff_seq auth_pos aff aff_val cor_afid given_seq cor1_given_name 10.1001/jama.2017.20952 85043226815 2018 List(List(1, 56813936800, auth, false, BA, cdcdf30c4c72a5f61c8eb00141555a59d0aac514, Theodore T., Theodore T., Lee T.T., Lee T.T., T.T., T.T., null, null, null, Lee, Lee), List(2, 6506525459, auth, false, MD, JD, MPH, null, Aaron S., Aaron S., Kesselheim A.S., Kesselheim A.S., A.S., A.S., null, null, null, Kesselheim, Kesselheim), List(3, 6506387711, auth, false, JD, null, Amy, Amy, Kapczynski A., Kapczynski A., A., A., null, null, null, Kapczynski, Kapczynski)) List(List(1, 1, true), List(2, 2, true), List(3, 3, true)) List(List(1, 56813936800, null, false, BA, null, Theodore T., null, Lee T.T., null, T.T., null, null, null, null, Lee, null)) no None 00987484 List(null, null, usa, 06, 03, 6 March 2018, 2018, smcleod@itsa.ucsf.edu, email, null, null, null, List(15383598), null, List(00987484), American Medical Association, JAMA - Journal of the American Medical Association, JAMA, 85291, j, https://jamanetwork.com/journals/jama/articlepdf/2672841/jama_lee_2018_vp_170197.pdf) 41 List(List(usa, null)) List(List(127 Wall St, New Haven, null, United States, List(60005455), List(Yale Law School, Yale University), 2, 06511, CT, usa, null, 60005455, 103317903), List(null, Boston, null, United States, List(60002746, 60016782), List(Program On Regulation, Therapeutics, and Law (PORTAL), Division of Pharmacoepidemiology and Pharmacoeconomics, Department of Medicine, Brigham and Women’s Hospital, Harvard Medical School), 7, null, MA, usa, null, 60002746, 118978541), List(null, New Haven, null, United States, List(60005455), List(Collaboration for Research Integrity and Transparency (CRIT), Yale Law School), 2, null, CT, usa, null, 60005455, 119725525)) List(1, 56813936800, auth, false, BA, cdcdf30c4c72a5f61c8eb00141555a59d0aac514, Theodore T., Theodore T., Lee T.T., Lee T.T., T.T., T.T., null, null, null, Lee, Lee) List(3, 6506387711, auth, false, JD, null, Amy, Amy, Kapczynski A., Kapczynski A., A., A., null, null, null, Kapczynski, Kapczynski) 3 56813936800 6506387711 List(56813936800) List(1) 1 List(1, 2, 3) List(1, 2, 3) 1 1 List(127 Wall St, New Haven, null, United States, List(60005455), List(Yale Law School, Yale University), 2, 06511, CT, usa, null, 60005455, 103317903) 60005455 List(Theodore T., Aaron S., Amy) Theodore T. 10.1001/jama.2017.21752 85042047525 2018 List(List(1, 57200639953, auth, false, null, 5466620b210ccb9fef349e079b265a00510239f1, Jennifer R., Jennifer R., Henneman J.R., Henneman J., J.R., J.R., null, null, null, Henneman, Henneman)) List(List(1, 1, true)) List(List(1, 57200639953, null, false, null, null, Jennifer R., null, Henneman J.R., null, J.R., null, null, null, null, Henneman, null)) ar None 00987484 List(null, null, usa, 13, 02, 13 February 2018, 2018, smcleod@itsa.ucsf.edu, email, null, null, null, List(15383598), null, List(00987484), American Medical Association, JAMA - Journal of the American Medical Association, JAMA, 85291, j, https://jamanetwork.com/journals/jama/currentissue) 0 List(List(usa, null)) List(List(100 W Ave Pkwy, Denver, null, United States, List(101141036), List(Petrie Institute of Western American Art, Denver Art Museum), 2, 80204, CO, usa, null, 101141036, 106764742)) List(1, 57200639953, auth, false, null, 5466620b210ccb9fef349e079b265a00510239f1, Jennifer R., Jennifer R., Henneman J.R., Henneman J., J.R., J.R., null, null, null, Henneman, Henneman) List(1, 57200639953, auth, false, null, 5466620b210ccb9fef349e079b265a00510239f1, Jennifer R., Jennifer R., Henneman J.R., Henneman J., J.R., J.R., null, null, null, Henneman, Henneman) 1 57200639953 57200639953 List(57200639953) List(1) 1 List(1) List(1) 1 1 List(100 W Ave Pkwy, Denver, null, United States, List(101141036), List(Petrie Institute of Western American Ar

'len of xxx '5941314'\n''len of xxx '569819'\n''no of not null cor au'5941314'\n'5933027'\n'5933027'\n'

Eid cor_gender doi news_cnt Au year publication_type openaccess issn num_au Au1_id Au2_id Au_cor_id srcid subfield_article subfield_journal subfield_hybrid Au1_gender Au2_gender cor_au1 correspondence cor1_given_name cor_afid TopicId 84961226628 unknown 10.1016/j.resconrec.2016.03.007 0 List(List(1, 55924882600, auth, false, null, 7df62066aefcbeac922958fe9a15aa149c77905d, Ye, Ye, Li Y., Li Y., Y., Y., null, null, null, Li, Li), List(2, 57184720700, auth, false, null, 822d32e4913890b657bc44eb7ea8b3c05cb11b23, Qing, Qing, He Q., He Q., Q., Q., null, null, null, He, He), List(3, 57072127000, auth, false, null, a4eb2b2aa959d3b99ac80146df5c2e71b0a845d1, Xiao, Xiao, Luo X., Luo X., X., X., null, 0000-0001-6122-2211, null, Luo, Luo), List(4, 57038892100, auth, false, null, 03de14adb487bda321f77861e013682b17df1d7a, Yiran, Yiran, Zhang Y., Zhang Y., Y., Y., null, null, null, Zhang, Zhang), List(5, 55752935000, auth, false, null, 825f36c32d8481f324a413e77e02ee994b93e8d2, Liang, Liang, Dong L., Dong L., L., L., null, null, null, Dong, Dong)) 2018 ar None 09213449 5 55924882600 55752935000 List(57072127000) 26424 environmental sciences environmental sciences environmental sciences unknown unknown 57072127000 List(List(chn, null)) Xiao 60073652 59694 84971656750 male 10.1016/j.jasrep.2016.05.052 0 List(List(1, 7101995035, auth, false, null, null, Gunilla, Gunilla, Eriksson G., Eriksson G., G., G., null, 0000-0002-9926-6524, null, Eriksson, Eriksson), List(2, 15749241800, auth, false, null, null, Karin Margarita, Karin Margarita, Frei K.M., Frei K.M., K.M., K.M., null, null, null, Frei, Frei), List(3, 55318651600, auth, false, null, null, Rachel, Rachel, Howcroft R., Howcroft R., R., R., null, null, null, Howcroft, Howcroft), List(4, 57189522948, auth, false, null, null, Sara, Sara, Gummesson S., Gummesson S., S., S., null, null, null, Gummesson, Gummesson), List(5, 57189521040, auth, false, null, null, Fredrik, Fredrik, Molin F., Molin F., F., F., null, null, null, Molin, Molin), List(6, 7003643642, auth, false, null, null, Kerstin, Kerstin, Liden K., Lidén K., K., K., null, null, null, Lidén, Lidén), List(7, 7103231290, auth, false, null, null, Robert, Robert, Frei R., Frei R., R., R., null, null, null, Frei, Frei), List(8, 55318039900, auth, false, null, ec6b2f43c1c15e022a30a3dd58303b66d0e57706, Fredrik, Fredrik, Hallgren F., Hallgren F., F., F., null, null, null, Hallgren, Hallgren)) 2018 ar None 2352409X 8 7101995035 55318039900 List(55318039900) 21100369721 archaeology archaeology archaeology female male 55318039900 List(List(swe, null)) Fredrik 116739376 3394 84975129749 male 10.1016/j.ecss.2016.05.019 0 List(List(1, 7102119738, auth, false, null, 94530784ea84f2275f8b6490e17285dc36405963, Myron A., Myron A., Peck M.A., Peck M.A., M.A., M.A., null, null, null, Peck, Peck), List(2, 6602439394, auth, false, null, null, Christos, Christos, Arvanitidis C., Arvanitidis C., C., C., null, null, null, Arvanitidis, Arvanitidis), List(3, 36156979600, auth, false, null, null, Momme, Momme, Butenschon M., Butenschön M., M., M., null, null, null, Butenschön, Butenschön), List(4, 57208816987, auth, false, null, null, Donata Melaku, Donata Melaku, Canu D.M., Canu D.M., D.M., D.M., null, null, null, Canu, Canu), List(5, 9737818000, auth, false, null, null, Eva, Eva, Chatzinikolaou E., Chatzinikolaou E., E., E., null, null, null, Chatzinikolaou, Chatzinikolaou), List(6, 6506416319, auth, false, null, null, Andrea, Andrea, Cucco A., Cucco A., A., A., null, null, null, Cucco, Cucco), List(7, 55901479500, auth, false, null, null, Paolo, Paolo, Domenici P., Domenici P., P., P., null, null, null, Domenici, Domenici), List(8, 24553992900, auth, false, null, null, Jose A., Jose A., Fernandes J.A., Fernandes J.A., J.A., J.A., null, null, null, Fernandes, Fernandes), List(9, 54385035400, auth, false, null, null, Loic, Loic, Gasche L., Gasche L., L., L., null, null, null, Gasche, Gasche), List(10, 25230018900, auth, false, null, null, Klaus B., Klaus B., Hueber

'len of merged data between src '5842542'\n'

metrics_calculations sourcetitle openaccess_status srcid doi news_cnt year publication_type issn num_au Au1_id subfield_article subfield_journal Au1_gender TopicId cor_gender cor_au1 correspondence cor1_given_name cor_afid SJR_lst year_SJR pos SJR cor_af cor_coun country_name afid preferred_name sort_name address_part postal_code city state country country_tag name_variant org_domain org_type parent parent_preferred_name List(List(null, null, 2551.0, 1917.0, null, 334, 0.0, Complete, 1996, 6, 6), List(null, null, 2960.0, 2250.0, null, 315, 0.32, Complete, 1997, 4, 4), List(null, null, 3585.0, 2939.0, null, 371, 0.0, Complete, 1998, 7, 8), List(0.916, 1.131, 4101.0, 3220.0, null, 292, 0.0, Complete, 1999, 1, 2), List(0.952, 1.37, 4764.0, 3603.0, null, 529, 0.19, Complete, 2000, 6, 6), List(0.841, 1.245, 5902.0, 4332.0, null, 501, 0.2, Complete, 2001, 6, 6), List(1.099, 1.095, 6973.0, 5944.0, null, 315, 0.0, Complete, 2002, 2, 2), List(1.185, 1.377, 8868.0, 6978.0, null, 536, 0.19, Complete, 2003, 4, 4), List(1.327, 1.492, 10073.0, 8544.0, null, 440, 0.23, Complete, 2004, 4, 4), List(1.28, 1.844, 13860.0, 11251.0, null, 754, 0.27, Complete, 2005, 7, 9), List(1.359, 1.55, 16099.0, 13652.0, null, 723, 0.55, Complete, 2006, 9, 10), List(1.446, 1.575, 20367.0, 17021.0, null, 821, 1.46, Complete, 2007, 4, 6), List(1.448, 1.545, 22279.0, 18880.0, null, 838, 1.55, Complete, 2008, 4, 5), List(1.317, 1.524, 25562.0, 22134.0, null, 780, 1.28, Complete, 2009, 6, 6), List(1.434, 1.431, 28203.0, 24647.0, null, 776, 0.77, Complete, 2010, 3, 3), List(1.485, 1.729, 34314.0, 29987.0, List(List(19706, 6.0, 77, 3261, List(List(3105, List(90, 2), 98), List(2506, List(126, 5), 96), List(2505, List(233, 13), 94), List(2208, List(589, 35), 94), List(3104, List(383, 25), 93), List(2508, List(91, 7), 92), List(2504, List(183, 17), 90)))), 909, 1.1, Complete, 2011, 8, 8), List(1.412, 1.637, 36847.0, 32129.0, List(List(20977, 6.1, 76, 3451, List(List(3105, List(91, 2), 98), List(2506, List(127, 5), 96), List(3104, List(387, 24), 93), List(2505, List(234, 15), 93), List(2508, List(93, 7), 93), List(2208, List(615, 45), 92), List(2504, List(193, 17), 91)))), 1020, 1.27, Complete, 2012, 7, 10), List(1.261, 1.628, 42959.0, 36463.0, List(List(24104, 6.0, 77, 4034, List(List(3105, List(95, 2), 98), List(2506, List(136, 6), 95), List(3104, List(388, 27), 93), List(2505, List(240, 17), 93), List(2508, List(96, 8), 92), List(2208, List(631, 51), 91), List(2504, List(199, 19), 90)))), 1359, 1.32, Complete, 2013, 12, 12), List(1.229, 1.652, 49313.0, 42198.0, List(List(29686, 6.2, 81, 4781, List(List(3105, List(99, 2), 98), List(2506, List(137, 5), 96), List(2508, List(101, 7), 93), List(2505, List(249, 17), 93), List(3104, List(395, 28), 93), List(2208, List(651, 47), 92), List(2504, List(207, 18), 91)))), 1516, 0.99, Complete, 2014, 8, 10), List(1.225, 1.509, 55727.0, 48792.0, List(List(39508, 7.4, 85, 5332, List(List(3105, List(104, 1), 99), List(2506, List(141, 5), 96), List(2505, List(253, 13), 95), List(2508, List(105, 6), 94), List(2208, List(660, 37), 94), List(3104, List(401, 23), 94), List(2504, List(213, 16), 92)))), 1507, 1.13, Complete, 2015, 6, 6), List(1.343, 1.462, 64086.0, 55967.0, List(List(51317, 8.6, 88, 5954, List(List(3105, List(106, 1), 99), List(2506, List(145, 5), 96), List(2508, List(110, 5), 95), List(2505, List(253, 11), 95), List(3104, List(402, 20), 95), List(2208, List(654, 34), 94), List(2504, List(219, 17), 92)))), 1630, 1.1, Complete, 2016, 3, 3), List(1.406, 1.459, 72220.0, 62098.0, List(List(63159, 9.3, 88, 6814, List(List(3105, List(123, 1), 99), List(2506, List(152, 5), 97), List(2508, List(117, 5), 96), List(3104, List(395, 20), 95), List(2505, List(270, 14), 95), List(2208, List(666, 35), 94), List(2504, List(225, 17), 92)))), 2196, 1.32, Complete, 2017, 14, 15), List(1.389, 1.488, 88183.0, 75400.0, List(List(74910, 9.4, 87, 7949, List(List(3105, List(125, 2), 98), List(2506, List(150, 6), 96), List(3104, List(398, 20), 95), Li

'len of data whose cor_gender is not unknown '4792464'\n'

metrics_calculations sourcetitle openaccess_status srcid doi news_cnt year publication_type issn num_au Au1_id subfield_article subfield_journal Au1_gender TopicId cor_gender cor_au1 correspondence cor1_given_name cor_afid SJR_lst year_SJR pos SJR cor_af cor_coun country_name afid preferred_name sort_name address_part postal_code city state country country_tag name_variant org_domain org_type parent parent_preferred_name List(List(null, null, 2551.0, 1917.0, null, 334, 0.0, Complete, 1996, 6, 6), List(null, null, 2960.0, 2250.0, null, 315, 0.32, Complete, 1997, 4, 4), List(null, null, 3585.0, 2939.0, null, 371, 0.0, Complete, 1998, 7, 8), List(0.916, 1.131, 4101.0, 3220.0, null, 292, 0.0, Complete, 1999, 1, 2), List(0.952, 1.37, 4764.0, 3603.0, null, 529, 0.19, Complete, 2000, 6, 6), List(0.841, 1.245, 5902.0, 4332.0, null, 501, 0.2, Complete, 2001, 6, 6), List(1.099, 1.095, 6973.0, 5944.0, null, 315, 0.0, Complete, 2002, 2, 2), List(1.185, 1.377, 8868.0, 6978.0, null, 536, 0.19, Complete, 2003, 4, 4), List(1.327, 1.492, 10073.0, 8544.0, null, 440, 0.23, Complete, 2004, 4, 4), List(1.28, 1.844, 13860.0, 11251.0, null, 754, 0.27, Complete, 2005, 7, 9), List(1.359, 1.55, 16099.0, 13652.0, null, 723, 0.55, Complete, 2006, 9, 10), List(1.446, 1.575, 20367.0, 17021.0, null, 821, 1.46, Complete, 2007, 4, 6), List(1.448, 1.545, 22279.0, 18880.0, null, 838, 1.55, Complete, 2008, 4, 5), List(1.317, 1.524, 25562.0, 22134.0, null, 780, 1.28, Complete, 2009, 6, 6), List(1.434, 1.431, 28203.0, 24647.0, null, 776, 0.77, Complete, 2010, 3, 3), List(1.485, 1.729, 34314.0, 29987.0, List(List(19706, 6.0, 77, 3261, List(List(3105, List(90, 2), 98), List(2506, List(126, 5), 96), List(2505, List(233, 13), 94), List(2208, List(589, 35), 94), List(3104, List(383, 25), 93), List(2508, List(91, 7), 92), List(2504, List(183, 17), 90)))), 909, 1.1, Complete, 2011, 8, 8), List(1.412, 1.637, 36847.0, 32129.0, List(List(20977, 6.1, 76, 3451, List(List(3105, List(91, 2), 98), List(2506, List(127, 5), 96), List(3104, List(387, 24), 93), List(2505, List(234, 15), 93), List(2508, List(93, 7), 93), List(2208, List(615, 45), 92), List(2504, List(193, 17), 91)))), 1020, 1.27, Complete, 2012, 7, 10), List(1.261, 1.628, 42959.0, 36463.0, List(List(24104, 6.0, 77, 4034, List(List(3105, List(95, 2), 98), List(2506, List(136, 6), 95), List(3104, List(388, 27), 93), List(2505, List(240, 17), 93), List(2508, List(96, 8), 92), List(2208, List(631, 51), 91), List(2504, List(199, 19), 90)))), 1359, 1.32, Complete, 2013, 12, 12), List(1.229, 1.652, 49313.0, 42198.0, List(List(29686, 6.2, 81, 4781, List(List(3105, List(99, 2), 98), List(2506, List(137, 5), 96), List(2508, List(101, 7), 93), List(2505, List(249, 17), 93), List(3104, List(395, 28), 93), List(2208, List(651, 47), 92), List(2504, List(207, 18), 91)))), 1516, 0.99, Complete, 2014, 8, 10), List(1.225, 1.509, 55727.0, 48792.0, List(List(39508, 7.4, 85, 5332, List(List(3105, List(104, 1), 99), List(2506, List(141, 5), 96), List(2505, List(253, 13), 95), List(2508, List(105, 6), 94), List(2208, List(660, 37), 94), List(3104, List(401, 23), 94), List(2504, List(213, 16), 92)))), 1507, 1.13, Complete, 2015, 6, 6), List(1.343, 1.462, 64086.0, 55967.0, List(List(51317, 8.6, 88, 5954, List(List(3105, List(106, 1), 99), List(2506, List(145, 5), 96), List(2508, List(110, 5), 95), List(2505, List(253, 11), 95), List(3104, List(402, 20), 95), List(2208, List(654, 34), 94), List(2504, List(219, 17), 92)))), 1630, 1.1, Complete, 2016, 3, 3), List(1.406, 1.459, 72220.0, 62098.0, List(List(63159, 9.3, 88, 6814, List(List(3105, List(123, 1), 99), List(2506, List(152, 5), 97), List(2508, List(117, 5), 96), List(3104, List(395, 20), 95), List(2505, List(270, 14), 95), List(2208, List(666, 35), 94), List(2504, List(225, 17), 92)))), 2196, 1.32, Complete, 2017, 14, 15), List(1.389, 1.488, 88183.0, 75400.0, List(List(74910, 9.4, 87, 7949, List(List(3105, List(125, 2), 98), List(2506, List(150, 6), 96), List(3104, List(398, 20), 95), Li

'len of unknown name '989940'\n''len of unknown name after dropping null country and given name '963009'\n''len or merged gender with wos '596600'\n'

In [0]:
ddf2 = newfile.drop("cor_gender")
ddf3 = ddf2.withColumnRenamed("gender", "cor_gender")
#ddf3.printSchema()
#display(ddf3.select('cor_gender').distinct())
ddf4 = ddf3.select('srcid','openaccess_status','doi','news_cnt','year','issn','num_au','cor_gender','TopicId','Au1_gender','country_name','SJR','subfield_article','preferred_name','org_type','cor_au1').toPandas()
print(ddf4.head(5)) 

ddfx = val_data.select('srcid','openaccess_status','doi','news_cnt','year','issn','num_au','cor_gender','TopicId','Au1_gender','country_name','SJR','subfield_article','preferred_name','org_type','cor_au1').toPandas()
display(len(ddfx),"\n")
display(len(ddf4),"\n")
ddf = ddfx.append(ddf4, ignore_index = True)
display(len(ddf),"\n")

         srcid openaccess_status                            doi  news_cnt  \
0  18300156731                NO     10.1038/s41585-020-00382-9         2   
1  21100406908                NO      10.1016/j.euf.2019.04.011         0   
2        13205                NO  10.1016/j.urolonc.2019.09.006         0   
3  19700182758               YES     10.1038/s41467-020-17965-0         0   
4        13205                NO  10.1016/j.urolonc.2020.07.019         0   

   year      issn  num_au cor_gender  TopicId Au1_gender   country_name  \
0  2020  17594812       8          M     6127       male  United States   
1  2019  24054569       9          M     3802       male  United States   
2  2019  10781439      12          M     2740       male  United States   
3  2020  20411723      17          M      403    unknown  United States   
4  2020  10781439      19          M     5210       male  United States   

     SJR           subfield_article                          preferred_name  \
0  1.97

In [0]:
###new version
smc = spark.read.format("csv").option("header", "true").load("dbfs:/FileStore/shared_uploads/arabi2@wisc.edu/sm_journal_classification.csv")
smc = smc.select('Domain_English','Field_English','SubField_English').toPandas()
smc = smc.dropna()
smc = smc.drop_duplicates()
print(len(smc))
smc['SubField_English'] = smc['SubField_English'].str.lower()
ddf['subfield_article'] = ddf['subfield_article'].str.lower()

#print(smc.dtypes)
total = smc.merge(ddf,left_on='SubField_English',right_on = 'subfield_article',how = 'inner')
print(len(total))

175
5373320


In [0]:
us = total[total['country_name'] == 'United States']
print(len(us))
t1 = us[us.news_cnt > 0]
print("len of t1 ",len(t1))
t1 = t1.drop(columns = ['srcid','openaccess_status','issn','num_au','TopicId','Au1_gender','country_name','SJR','subfield_article','preferred_name','org_type',
                        'Domain_English','Field_English','SubField_English'], axis = 1)
#print(t1['news_cnt'].sum())

ret = spark.read.format("csv").option("header", "true").load("dbfs:/FileStore/shared_uploads/arabi2@wisc.edu/retrected_doi_wos.csv")
retracted = ret.select('doi').toPandas()
ids_to_remove = retracted['doi']
t1 = t1[~t1['doi'].isin(ids_to_remove)]
print("len of t1 after removing retracted dois ", len(t1))

df_apr = spark.read.format("parquet").load(basePath+tablename_apr)
df_apr = df_apr.select('auid','given_name_pn','surname_pn','indexed_name_pn').toPandas()
t2 = t1.merge(df_apr, left_on = "cor_au1",right_on="auid", how = "inner")
print("len of t2 ",len(t2))

#print(t1['doi'])
spark_df = spark.createDataFrame(t2)
display(spark_df)


1014175
len of t1  129451
len of t1 after removing retracted dois  129440
len of t2  129437


doi news_cnt year cor_gender cor_au1 auid given_name_pn surname_pn indexed_name_pn 10.1126/science.aaz5670 14 2019 male 7006567885 7006567885 Noah G. Fierer Fierer N. 10.1021/acs.est.1c03309 1 2021 male 7006567885 7006567885 Noah G. Fierer Fierer N. 10.1128/mbio.01614-18 51 2018 male 7006567885 7006567885 Noah G. Fierer Fierer N. 10.3389/fsufs.2020.577723 21 2020 male 56002786300 56002786300 Peter Newton Newton P. 10.3389/fsufs.2021.624270 5 2021 male 56002786300 56002786300 Peter Newton Newton P. 10.1073/pnas.1818400116 7 2019 male 35179276400 35179276400 Manuel Delgado-Baquerizo Delgado-Baquerizo M. 10.1126/science.aap9516 44 2018 male 35179276400 35179276400 Manuel Delgado-Baquerizo Delgado-Baquerizo M. 10.1111/gcbb.12805 15 2021 male 7102845750 7102845750 John C. Cushman Cushman J. 10.1111/tpj.14783 5 2020 male 7102845750 7102845750 John C. Cushman Cushman J. 10.1002/saj2.20349 3 2022 female 55793093000 55793093000 Emily E. Oldfield Oldfield E. 10.1016/j.soilbio.2018.06.014 1 2018 female 55793093000 55793093000 Emily E. Oldfield Oldfield E. 10.1126/science.abl7991 1 2022 female 55793093000 55793093000 Emily E. Oldfield Oldfield E. 10.1038/s41561-020-0634-x 10 2020 male 7402711360 7402711360 Steven J. Hall Hall S. 10.1073/pnas.2112108118 14 2021 male 7402711360 7402711360 Steven J. Hall Hall S. 10.1002/ecy.3113 1 2020 male 7402711360 7402711360 Steven J. Hall Hall S. 10.1007/s11104-019-04292-7 6 2019 male 7402711360 7402711360 Steven J. Hall Hall S. 10.1111/gcbb.12657 6 2020 male 7402711360 7402711360 Steven J. Hall Hall S. 10.1111/gcb.15867 5 2021 male 7402711360 7402711360 Steven J. Hall Hall S. 10.1073/pnas.1820334116 1 2019 male 12042621900 12042621900 Ludovico Cademartiri Cademartiri L. 10.1111/gcbb.12870 1 2021 male 55228996700 55228996700 Andy VanLoocke VanLoocke A. 10.1371/journal.pone.0219847 22 2019 female 56221750700 56221750700 Virginia A. Nichols Nichols V. 10.1002/saj2.20007 18 2020 male 57014532700 57014532700 Mriganka De De M. 10.1111/gcbb.12516 2 2018 female 56652009600 56652009600 Elke Brandes Brandes E. 10.2134/agronj2018.04.0297 1 2019 male 7004062175 7004062175 Mark A. Licht Licht M. 10.1016/j.jenvman.2019.109582 1 2019 female 10739701600 10739701600 Michelle L. Soupir Soupir M. 10.1038/s41598-020-80820-1 2 2021 female 57115681500 57115681500 Guiping Hu Hu G. 10.1002/agj2.20129 4 2020 male 55155422000 55155422000 Marshall D. McDaniel McDaniel M. 10.1038/s41893-019-0393-0 7 2019 male 12792326700 12792326700 Michael J. Castellano Castellano M. 10.1017/wet.2022.56 4 2022 male 14622356700 14622356700 Kevin W. Bradley Bradley K. 10.1017/inp.2020.2 10 2020 male 14622356700 14622356700 Kevin W. Bradley Bradley K. 10.1007/s00267-018-0998-5 2 2018 female 26665950700 26665950700 Caroline C. Brock Brock C. 10.3390/su13168682 1 2021 female 26665950700 26665950700 Caroline C. Brock Brock C. 10.1017/wet.2020.138 8 2021 female 57194219564 57194219564 Mandy D. Bish Bish M. 10.2134/jeq2019.05.0197 1 2019 female 57194219564 57194219564 Mandy D. Bish Bish M. 10.1371/journal.pone.0261989 31 2022 male 57052206500 57052206500 Jordon Wade Wade J. 10.1016/j.compag.2019.04.007 3 2019 male 7003394615 7003394615 Kenneth A. Sudduth Sudduth K. 10.1016/j.soilbio.2018.02.023 2 2018 male 7101862412 7101862412 Dafeng Hui Hui D. 10.3389/fenvs.2018.00066 4 2018 male 6602070842 6602070842 Teamrat A. Ghezzehei Ghezzehei T. 10.1002/jeq2.20270 4 2021 female 57224922844 57224922844 Yocelyn B. Villa Villa Y. 10.3389/fenvs.2018.00098 12 2018 male 57202252670 57202252670 Nathaniel A. Bogie Bogie N. 10.1016/j.jenvman.2021.112409 19 2021 female 57223228438 57223228438 Samantha L. Mosier Mosier S. 10.1002/ael2.20023 4 2020 female 57193380347 57193380347 Grace Lloyd Miner Miner G. 10.1038/s41598-019-47861-7 36 2019 male 7004593987 7004593987 Stephen M. Ogle Ogle S. 10.1186/s13021-018-0095-3 5 2018 male 7004593987 7004593987 Stephen M. Ogle Ogle S. 10.1038/s41558-021-01040-7 1 2021 male 7004593987 7004593987 Stephen M. Ogle Ogle S. 10.1016/j.worlddev

In [0]:
df_export = spark_df

In [0]:
%run /Snippets/footer_latest